# Language Translation
In this project, you’re going to take a peek into the realm of neural network machine translation.  You’ll be training a sequence to sequence model on a dataset of English and French sentences that can translate new sentences from English to French.
## Get the Data
Since translating the whole language of English to French will take lots of time to train, we have provided you with a small portion of the English corpus.

In [50]:
"""
DON'T MODIFY ANYTHING IN THIS CELL
"""
import helper
import problem_unittests as tests

source_path = 'data/small_vocab_en'
target_path = 'data/small_vocab_fr'
source_text = helper.load_data(source_path)
target_text = helper.load_data(target_path)

## Explore the Data
Play around with view_sentence_range to view different parts of the data.

In [51]:
view_sentence_range = (0, 10)

"""
DON'T MODIFY ANYTHING IN THIS CELL
"""
import numpy as np

print('Dataset Stats')
print('Roughly the number of unique words: {}'.format(len({word: None for word in source_text.split()})))

sentences = source_text.split('\n')
word_counts = [len(sentence.split()) for sentence in sentences]
print('Number of sentences: {}'.format(len(sentences)))
print('Average number of words in a sentence: {}'.format(np.average(word_counts)))

print()
print('English sentences {} to {}:'.format(*view_sentence_range))
print('\n'.join(source_text.split('\n')[view_sentence_range[0]:view_sentence_range[1]]))
print()
print('French sentences {} to {}:'.format(*view_sentence_range))
print('\n'.join(target_text.split('\n')[view_sentence_range[0]:view_sentence_range[1]]))

Dataset Stats
Roughly the number of unique words: 227
Number of sentences: 137861
Average number of words in a sentence: 13.225277634719028

English sentences 0 to 10:
new jersey is sometimes quiet during autumn , and it is snowy in april .
the united states is usually chilly during july , and it is usually freezing in november .
california is usually quiet during march , and it is usually hot in june .
the united states is sometimes mild during june , and it is cold in september .
your least liked fruit is the grape , but my least liked is the apple .
his favorite fruit is the orange , but my favorite is the grape .
paris is relaxing during december , but it is usually chilly in july .
new jersey is busy during spring , and it is never hot in march .
our least liked fruit is the lemon , but my least liked is the grape .
the united states is sometimes busy during january , and it is sometimes warm in november .

French sentences 0 to 10:
new jersey est parfois calme pendant l' automne 

## Implement Preprocessing Function
### Text to Word Ids
As you did with other RNNs, you must turn the text into a number so the computer can understand it. In the function `text_to_ids()`, you'll turn `source_text` and `target_text` from words to ids.  However, you need to add the `<EOS>` word id at the end of each sentence from `target_text`.  This will help the neural network predict when the sentence should end.

You can get the `<EOS>` word id by doing:
```python
target_vocab_to_int['<EOS>']
```
You can get other word ids using `source_vocab_to_int` and `target_vocab_to_int`.

In [52]:
def text_to_ids(source_text, target_text, source_vocab_to_int, target_vocab_to_int):
    """
    Convert source and target text to proper word ids
    :param source_text: String that contains all the source text.
    :param target_text: String that contains all the target text.
    :param source_vocab_to_int: Dictionary to go from the source words to an id
    :param target_vocab_to_int: Dictionary to go from the target words to an id
    :return: A tuple of lists (source_id_text, target_id_text)
    """
    # TODO: Implement Function
    source_id_text=[]
    for sentence in source_text.split('\n'):
        source_id_text.append([source_vocab_to_int[word] for word in sentence.split()])
    target_id_text=[]
    for sentence in target_text.split('\n'):
        sentence_array=[target_vocab_to_int[word] for word in sentence.split()]
        sentence_array.append(target_vocab_to_int['<EOS>'])
        target_id_text.append(sentence_array)
  
    return (source_id_text, target_id_text)

"""
DON'T MODIFY ANYTHING IN THIS CELL THAT IS BELOW THIS LINE
"""
tests.test_text_to_ids(text_to_ids)

Tests Passed


### Preprocess all the data and save it
Running the code cell below will preprocess all the data and save it to file.

In [53]:
"""
DON'T MODIFY ANYTHING IN THIS CELL
"""
helper.preprocess_and_save_data(source_path, target_path, text_to_ids)

# Check Point
This is your first checkpoint. If you ever decide to come back to this notebook or have to restart the notebook, you can start from here. The preprocessed data has been saved to disk.

In [54]:
"""
DON'T MODIFY ANYTHING IN THIS CELL
"""
import numpy as np
import helper

(source_int_text, target_int_text), (source_vocab_to_int, target_vocab_to_int), _ = helper.load_preprocess()

### Check the Version of TensorFlow and Access to GPU
This will check to make sure you have the correct version of TensorFlow and access to a GPU

In [55]:
"""
DON'T MODIFY ANYTHING IN THIS CELL
"""
from distutils.version import LooseVersion
import warnings
import tensorflow as tf

# Check TensorFlow Version
assert LooseVersion(tf.__version__) in [LooseVersion('1.0.0'), LooseVersion('1.0.1')], 'This project requires TensorFlow version 1.0  You are using {}'.format(tf.__version__)
print('TensorFlow Version: {}'.format(tf.__version__))

# Check for a GPU
if not tf.test.gpu_device_name():
    warnings.warn('No GPU found. Please use a GPU to train your neural network.')
else:
    print('Default GPU Device: {}'.format(tf.test.gpu_device_name()))

TensorFlow Version: 1.0.0


/Users/bella/anaconda/envs/dlnd/lib/python3.6/site-packages/ipykernel_launcher.py:14: UserWarning: No GPU found. Please use a GPU to train your neural network.
  


## Build the Neural Network
You'll build the components necessary to build a Sequence-to-Sequence model by implementing the following functions below:
- `model_inputs`
- `process_decoding_input`
- `encoding_layer`
- `decoding_layer_train`
- `decoding_layer_infer`
- `decoding_layer`
- `seq2seq_model`

### Input
Implement the `model_inputs()` function to create TF Placeholders for the Neural Network. It should create the following placeholders:

- Input text placeholder named "input" using the TF Placeholder name parameter with rank 2.
- Targets placeholder with rank 2.
- Learning rate placeholder with rank 0.
- Keep probability placeholder named "keep_prob" using the TF Placeholder name parameter with rank 0.

Return the placeholders in the following the tuple (Input, Targets, Learing Rate, Keep Probability)

In [56]:
def model_inputs():
    """
    Create TF Placeholders for input, targets, and learning rate.
    :return: Tuple (input, targets, learning rate, keep probability)
    """
    # TODO: Implement Function
    inputs=tf.placeholder(tf.int32,[None,None],name="input")
    target=tf.placeholder(tf.int32,[None,None],name="target")
    learning_rate=tf.placeholder(tf.float32,name="learning_rate")
    keep_prob=tf.placeholder(tf.float32,name="keep_prob")
    return inputs, target, learning_rate, keep_prob

"""
DON'T MODIFY ANYTHING IN THIS CELL THAT IS BELOW THIS LINE
"""
tests.test_model_inputs(model_inputs)

Tests Passed


### Process Decoding Input
Implement `process_decoding_input` using TensorFlow to remove the last word id from each batch in `target_data` and concat the GO ID to the beginning of each batch.

In [73]:
def process_decoding_input(target_data, target_vocab_to_int, batch_size):
    """
    Preprocess target data for decoding
    :param target_data: Target Placeholder
    :param target_vocab_to_int: Dictionary to go from the target words to an id
    :param batch_size: Batch Size
    :return: Preprocessed target data
    """
    
    # TODO: Implement Function
    
    ending = tf.strided_slice(target_data, [0, 0], [batch_size, -1], [1, 1])
    dec_input = tf.concat([tf.fill([batch_size, 1], target_vocab_to_int['<GO>']), ending], 1)
    return dec_input

"""
DON'T MODIFY ANYTHING IN THIS CELL THAT IS BELOW THIS LINE
"""
tests.test_process_decoding_input(process_decoding_input)

Tests Passed


### Encoding
Implement `encoding_layer()` to create a Encoder RNN layer using [`tf.nn.dynamic_rnn()`](https://www.tensorflow.org/api_docs/python/tf/nn/dynamic_rnn).

In [58]:
def encoding_layer(rnn_inputs, rnn_size, num_layers, keep_prob):
    """
    Create encoding layer
    :param rnn_inputs: Inputs for the RNN
    :param rnn_size: RNN Size
    :param num_layers: Number of layers
    :param keep_prob: Dropout keep probability
    :return: RNN state
    """
    lstm = tf.contrib.rnn.BasicLSTMCell(rnn_size)
    cell = tf.contrib.rnn.MultiRNNCell([lstm] * num_layers)
    drop = tf.contrib.rnn.DropoutWrapper(cell, output_keep_prob=keep_prob)
    (output,initial_state)=tf.nn.dynamic_rnn(drop,rnn_inputs,dtype=tf.float32)
    return  initial_state

"""
DON'T MODIFY ANYTHING IN THIS CELL THAT IS BELOW THIS LINE
"""
tests.test_encoding_layer(encoding_layer)

Tests Passed


### Decoding - Training
Create training logits using [`tf.contrib.seq2seq.simple_decoder_fn_train()`](https://www.tensorflow.org/versions/r1.0/api_docs/python/tf/contrib/seq2seq/simple_decoder_fn_train) and [`tf.contrib.seq2seq.dynamic_rnn_decoder()`](https://www.tensorflow.org/versions/r1.0/api_docs/python/tf/contrib/seq2seq/dynamic_rnn_decoder).  Apply the `output_fn` to the [`tf.contrib.seq2seq.dynamic_rnn_decoder()`](https://www.tensorflow.org/versions/r1.0/api_docs/python/tf/contrib/seq2seq/dynamic_rnn_decoder) outputs.

In [59]:
def decoding_layer_train(encoder_state, dec_cell, dec_embed_input, sequence_length, decoding_scope,
                         output_fn, keep_prob):
    """
    Create a decoding layer for training
    :param encoder_state: Encoder State
    :param dec_cell: Decoder RNN Cell
    :param dec_embed_input: Decoder embedded input
    :param sequence_length: Sequence Length
    :param decoding_scope: TenorFlow Variable Scope for decoding
    :param output_fn: Function to apply the output layer
    :param keep_prob: Dropout keep probability
    :return: Train Logits
    """
    # TODO: Implement Function
    drop = tf.contrib.rnn.DropoutWrapper(dec_cell, output_keep_prob=keep_prob)
    train_decoder_fn = tf.contrib.seq2seq.simple_decoder_fn_train(encoder_state)
    train_pred, _, _ = tf.contrib.seq2seq.dynamic_rnn_decoder(
    drop, train_decoder_fn, dec_embed_input, sequence_length, scope=decoding_scope)

    # Apply output function
    train_logits =  output_fn(train_pred)
    return train_logits


"""
DON'T MODIFY ANYTHING IN THIS CELL THAT IS BELOW THIS LINE
"""
tests.test_decoding_layer_train(decoding_layer_train)

Tests Passed


### Decoding - Inference
Create inference logits using [`tf.contrib.seq2seq.simple_decoder_fn_inference()`](https://www.tensorflow.org/versions/r1.0/api_docs/python/tf/contrib/seq2seq/simple_decoder_fn_inference) and [`tf.contrib.seq2seq.dynamic_rnn_decoder()`](https://www.tensorflow.org/versions/r1.0/api_docs/python/tf/contrib/seq2seq/dynamic_rnn_decoder). 

In [60]:
def decoding_layer_infer(encoder_state, dec_cell, dec_embeddings, start_of_sequence_id, end_of_sequence_id,
                         maximum_length, vocab_size, decoding_scope, output_fn, keep_prob):
    """
    Create a decoding layer for inference
    :param encoder_state: Encoder state
    :param dec_cell: Decoder RNN Cell
    :param dec_embeddings: Decoder embeddings
    :param start_of_sequence_id: GO ID
    :param end_of_sequence_id: EOS Id
    :param maximum_length: The maximum allowed time steps to decode
    :param vocab_size: Size of vocabulary
    :param decoding_scope: TensorFlow Variable Scope for decoding
    :param output_fn: Function to apply the output layer
    :param keep_prob: Dropout keep probability
    :return: Inference Logits
    """
    # TODO: Implement Function
    infer_decoder_fn = tf.contrib.seq2seq.simple_decoder_fn_inference(
    output_fn, encoder_state, dec_embeddings, start_of_sequence_id, end_of_sequence_id, 
    maximum_length - 1, vocab_size)
    drop = tf.contrib.rnn.DropoutWrapper(dec_cell, output_keep_prob=keep_prob)
    inference_logits, _, _ = tf.contrib.seq2seq.dynamic_rnn_decoder(drop, infer_decoder_fn, scope=decoding_scope)
    return inference_logits


"""
DON'T MODIFY ANYTHING IN THIS CELL THAT IS BELOW THIS LINE
"""
tests.test_decoding_layer_infer(decoding_layer_infer)

Tests Passed


### Build the Decoding Layer
Implement `decoding_layer()` to create a Decoder RNN layer.

- Create RNN cell for decoding using `rnn_size` and `num_layers`.
- Create the output fuction using [`lambda`](https://docs.python.org/3/tutorial/controlflow.html#lambda-expressions) to transform it's input, logits, to class logits.
- Use the your `decoding_layer_train(encoder_state, dec_cell, dec_embed_input, sequence_length, decoding_scope, output_fn, keep_prob)` function to get the training logits.
- Use your `decoding_layer_infer(encoder_state, dec_cell, dec_embeddings, start_of_sequence_id, end_of_sequence_id, maximum_length, vocab_size, decoding_scope, output_fn, keep_prob)` function to get the inference logits.

Note: You'll need to use [tf.variable_scope](https://www.tensorflow.org/api_docs/python/tf/variable_scope) to share variables between training and inference.

In [61]:
def decoding_layer(dec_embed_input, dec_embeddings, encoder_state, vocab_size, sequence_length, rnn_size,
                   num_layers, target_vocab_to_int, keep_prob):
    """
    Create decoding layer
    :param dec_embed_input: Decoder embedded input
    :param dec_embeddings: Decoder embeddings
    :param encoder_state: The encoded state
    :param vocab_size: Size of vocabulary
    :param sequence_length: Sequence Length
    :param rnn_size: RNN Size
    :param num_layers: Number of layers
    :param target_vocab_to_int: Dictionary to go from the target words to an id
    :param keep_prob: Dropout keep probability
    :return: Tuple of (Training Logits, Inference Logits)
    """
    # RNN
    dec_cell = tf.contrib.rnn.MultiRNNCell([tf.contrib.rnn.BasicLSTMCell(rnn_size)] * num_layers)
      
    with tf.variable_scope("decoding") as decoding_scope:
        output_fn = lambda x: tf.contrib.layers.fully_connected(x, vocab_size, None, scope=decoding_scope)
        logits = decoding_layer_train(encoder_state, dec_cell, dec_embed_input, sequence_length, decoding_scope,
                         output_fn, keep_prob)
    with tf.variable_scope("decoding",reuse=True) as decoding_scope:
        infer=decoding_layer_infer(encoder_state, dec_cell, dec_embeddings, target_vocab_to_int["<GO>"], target_vocab_to_int["<EOS>"],
                         sequence_length, vocab_size, decoding_scope, output_fn, keep_prob)
    return logits, infer


"""
DON'T MODIFY ANYTHING IN THIS CELL THAT IS BELOW THIS LINE
"""
tests.test_decoding_layer(decoding_layer)

Tests Passed


### Build the Neural Network
Apply the functions you implemented above to:

- Apply embedding to the input data for the encoder.
- Encode the input using your `encoding_layer(rnn_inputs, rnn_size, num_layers, keep_prob)`.
- Process target data using your `process_decoding_input(target_data, target_vocab_to_int, batch_size)` function.
- Apply embedding to the target data for the decoder.
- Decode the encoded input using your `decoding_layer(dec_embed_input, dec_embeddings, encoder_state, vocab_size, sequence_length, rnn_size, num_layers, target_vocab_to_int, keep_prob)`.

In [62]:
def seq2seq_model(input_data, target_data, keep_prob, batch_size, sequence_length, source_vocab_size, target_vocab_size,
                  enc_embedding_size, dec_embedding_size, rnn_size, num_layers, target_vocab_to_int):
    """
    Build the Sequence-to-Sequence part of the neural network
    :param input_data: Input placeholder
    :param target_data: Target placeholder
    :param keep_prob: Dropout keep probability placeholder
    :param batch_size: Batch Size
    :param sequence_length: Sequence Length
    :param source_vocab_size: Source vocabulary size
    :param target_vocab_size: Target vocabulary size
    :param enc_embedding_size: Decoder embedding size
    :param dec_embedding_size: Encoder embedding size
    :param rnn_size: RNN Size
    :param num_layers: Number of layers
    :param target_vocab_to_int: Dictionary to go from the target words to an id
    :return: Tuple of (Training Logits, Inference Logits)
    """
    # TODO: Implement Function
    enc_embed_input = tf.contrib.layers.embed_sequence(input_data, source_vocab_size, enc_embedding_size)
    enc_state = encoding_layer(enc_embed_input, rnn_size, num_layers, keep_prob)

    target_data = process_decoding_input(target_data, target_vocab_to_int, batch_size)
    dec_embeddings = tf.Variable(tf.random_uniform([target_vocab_size, dec_embedding_size]))
    dec_embed_input = tf.nn.embedding_lookup(dec_embeddings, target_data)

    return decoding_layer(dec_embed_input, dec_embeddings, enc_state, target_vocab_size, sequence_length, rnn_size,
                   num_layers, target_vocab_to_int, keep_prob)
    



"""
DON'T MODIFY ANYTHING IN THIS CELL THAT IS BELOW THIS LINE
"""
tests.test_seq2seq_model(seq2seq_model)

Tests Passed


## Neural Network Training
### Hyperparameters
Tune the following parameters:

- Set `epochs` to the number of epochs.
- Set `batch_size` to the batch size.
- Set `rnn_size` to the size of the RNNs.
- Set `num_layers` to the number of layers.
- Set `encoding_embedding_size` to the size of the embedding for the encoder.
- Set `decoding_embedding_size` to the size of the embedding for the decoder.
- Set `learning_rate` to the learning rate.
- Set `keep_probability` to the Dropout keep probability

In [63]:
# Number of Epochs
epochs = 1
# Batch Size
batch_size = 1
# RNN Size
rnn_size = 1
# Number of Layers
num_layers = 1
# Embedding Size
encoding_embedding_size = 1
decoding_embedding_size = 1
# Learning Rate
learning_rate = 0.01
# Dropout Keep Probability
keep_probability = 0.8

### Build the Graph
Build the graph using the neural network you implemented.

In [74]:
"""
DON'T MODIFY ANYTHING IN THIS CELL
"""
save_path = 'checkpoints/dev'
(source_int_text, target_int_text), (source_vocab_to_int, target_vocab_to_int), _ = helper.load_preprocess()
max_source_sentence_length = max([len(sentence) for sentence in source_int_text])

train_graph = tf.Graph()
with train_graph.as_default():
    input_data, targets, lr, keep_prob = model_inputs()
    sequence_length = tf.placeholder_with_default(max_source_sentence_length, None, name='sequence_length')
    input_shape = tf.shape(input_data)
    
    train_logits, inference_logits = seq2seq_model(
        tf.reverse(input_data, [-1]), targets, keep_prob, batch_size, sequence_length, len(source_vocab_to_int), len(target_vocab_to_int),
        encoding_embedding_size, decoding_embedding_size, rnn_size, num_layers, target_vocab_to_int)

    tf.identity(inference_logits, 'logits')
    with tf.name_scope("optimization"):
        # Loss function
        cost = tf.contrib.seq2seq.sequence_loss(
            train_logits,
            targets,
            tf.ones([input_shape[0], sequence_length]))

        # Optimizer
        optimizer = tf.train.AdamOptimizer(lr)

        # Gradient Clipping
        gradients = optimizer.compute_gradients(cost)
        capped_gradients = [(tf.clip_by_value(grad, -1., 1.), var) for grad, var in gradients if grad is not None]
        train_op = optimizer.apply_gradients(capped_gradients)

### Train
Train the neural network on the preprocessed data. If you have a hard time getting a good loss, check the forums to see if anyone is having the same problem.

In [ ]:
"""
DON'T MODIFY ANYTHING IN THIS CELL
"""
import time

def get_accuracy(target, logits):
    """
    Calculate accuracy
    """
    max_seq = max(target.shape[1], logits.shape[1])
    if max_seq - target.shape[1]:
        target = np.pad(
            target,
            [(0,0),(0,max_seq - target.shape[1])],
            'constant')
    if max_seq - logits.shape[1]:
        logits = np.pad(
            logits,
            [(0,0),(0,max_seq - logits.shape[1]), (0,0)],
            'constant')

    return np.mean(np.equal(target, np.argmax(logits, 2)))

train_source = source_int_text[batch_size:]
train_target = target_int_text[batch_size:]

valid_source = helper.pad_sentence_batch(source_int_text[:batch_size])
valid_target = helper.pad_sentence_batch(target_int_text[:batch_size])

with tf.Session(graph=train_graph) as sess:
    sess.run(tf.global_variables_initializer())

    for epoch_i in range(epochs):
        for batch_i, (source_batch, target_batch) in enumerate(
                helper.batch_data(train_source, train_target, batch_size)):
            start_time = time.time()
            
            _, loss = sess.run(
                [train_op, cost],
                {input_data: source_batch,
                 targets: target_batch,
                 lr: learning_rate,
                 sequence_length: target_batch.shape[1],
                 keep_prob: keep_probability})
            
            batch_train_logits = sess.run(
                inference_logits,
                {input_data: source_batch, keep_prob: 1.0})
            batch_valid_logits = sess.run(
                inference_logits,
                {input_data: valid_source, keep_prob: 1.0})
                
            train_acc = get_accuracy(target_batch, batch_train_logits)
            valid_acc = get_accuracy(np.array(valid_target), batch_valid_logits)
            end_time = time.time()
            print('Epoch {:>3} Batch {:>4}/{} - Train Accuracy: {:>6.3f}, Validation Accuracy: {:>6.3f}, Loss: {:>6.3f}'
                  .format(epoch_i, batch_i, len(source_int_text) // batch_size, train_acc, valid_acc, loss))

    # Save Model
    saver = tf.train.Saver()
    saver.save(sess, save_path)
    print('Model Trained and Saved')

Epoch   0 Batch    0/137861 - Train Accuracy:  0.000, Validation Accuracy:  0.000, Loss:  5.891
Epoch   0 Batch    1/137861 - Train Accuracy:  0.000, Validation Accuracy:  0.000, Loss:  5.869
Epoch   0 Batch    2/137861 - Train Accuracy:  0.000, Validation Accuracy:  0.000, Loss:  5.851
Epoch   0 Batch    3/137861 - Train Accuracy:  0.000, Validation Accuracy:  0.000, Loss:  5.860
Epoch   0 Batch    4/137861 - Train Accuracy:  0.000, Validation Accuracy:  0.000, Loss:  5.831
Epoch   0 Batch    5/137861 - Train Accuracy:  0.000, Validation Accuracy:  0.000, Loss:  5.809
Epoch   0 Batch    6/137861 - Train Accuracy:  0.000, Validation Accuracy:  0.000, Loss:  5.817
Epoch   0 Batch    7/137861 - Train Accuracy:  0.000, Validation Accuracy:  0.000, Loss:  5.786
Epoch   0 Batch    8/137861 - Train Accuracy:  0.000, Validation Accuracy:  0.000, Loss:  5.759
Epoch   0 Batch    9/137861 - Train Accuracy:  0.000, Validation Accuracy:  0.000, Loss:  5.798
Epoch   0 Batch   10/137861 - Train Accu

Epoch   0 Batch   88/137861 - Train Accuracy:  0.000, Validation Accuracy:  0.000, Loss:  4.540
Epoch   0 Batch   89/137861 - Train Accuracy:  0.000, Validation Accuracy:  0.000, Loss:  4.356
Epoch   0 Batch   90/137861 - Train Accuracy:  0.000, Validation Accuracy:  0.000, Loss:  4.613
Epoch   0 Batch   91/137861 - Train Accuracy:  0.000, Validation Accuracy:  0.000, Loss:  4.700
Epoch   0 Batch   92/137861 - Train Accuracy:  0.000, Validation Accuracy:  0.000, Loss:  4.619
Epoch   0 Batch   93/137861 - Train Accuracy:  0.000, Validation Accuracy:  0.000, Loss:  4.779
Epoch   0 Batch   94/137861 - Train Accuracy:  0.000, Validation Accuracy:  0.000, Loss:  4.717
Epoch   0 Batch   95/137861 - Train Accuracy:  0.000, Validation Accuracy:  0.000, Loss:  4.632
Epoch   0 Batch   96/137861 - Train Accuracy:  0.000, Validation Accuracy:  0.000, Loss:  4.902
Epoch   0 Batch   97/137861 - Train Accuracy:  0.000, Validation Accuracy:  0.000, Loss:  5.253
Epoch   0 Batch   98/137861 - Train Accu

Epoch   0 Batch  174/137861 - Train Accuracy:  0.118, Validation Accuracy:  0.000, Loss:  4.305
Epoch   0 Batch  175/137861 - Train Accuracy:  0.111, Validation Accuracy:  0.000, Loss:  4.366
Epoch   0 Batch  176/137861 - Train Accuracy:  0.118, Validation Accuracy:  0.000, Loss:  4.246
Epoch   0 Batch  177/137861 - Train Accuracy:  0.118, Validation Accuracy:  0.118, Loss:  4.526
Epoch   0 Batch  178/137861 - Train Accuracy:  0.118, Validation Accuracy:  0.118, Loss:  4.537
Epoch   0 Batch  179/137861 - Train Accuracy:  0.118, Validation Accuracy:  0.000, Loss:  4.348
Epoch   0 Batch  180/137861 - Train Accuracy:  0.100, Validation Accuracy:  0.118, Loss:  4.214
Epoch   0 Batch  181/137861 - Train Accuracy:  0.000, Validation Accuracy:  0.000, Loss:  5.786
Epoch   0 Batch  182/137861 - Train Accuracy:  0.000, Validation Accuracy:  0.000, Loss:  4.671
Epoch   0 Batch  183/137861 - Train Accuracy:  0.118, Validation Accuracy:  0.000, Loss:  4.317
Epoch   0 Batch  184/137861 - Train Accu

Epoch   0 Batch  261/137861 - Train Accuracy:  0.000, Validation Accuracy:  0.000, Loss:  4.055
Epoch   0 Batch  262/137861 - Train Accuracy:  0.000, Validation Accuracy:  0.000, Loss:  4.076
Epoch   0 Batch  263/137861 - Train Accuracy:  0.000, Validation Accuracy:  0.000, Loss:  4.155
Epoch   0 Batch  264/137861 - Train Accuracy:  0.000, Validation Accuracy:  0.000, Loss:  4.442
Epoch   0 Batch  265/137861 - Train Accuracy:  0.000, Validation Accuracy:  0.000, Loss:  4.194
Epoch   0 Batch  266/137861 - Train Accuracy:  0.000, Validation Accuracy:  0.000, Loss:  3.976
Epoch   0 Batch  267/137861 - Train Accuracy:  0.000, Validation Accuracy:  0.000, Loss:  4.538
Epoch   0 Batch  268/137861 - Train Accuracy:  0.000, Validation Accuracy:  0.000, Loss:  3.929
Epoch   0 Batch  269/137861 - Train Accuracy:  0.000, Validation Accuracy:  0.000, Loss:  4.471
Epoch   0 Batch  270/137861 - Train Accuracy:  0.000, Validation Accuracy:  0.000, Loss:  3.985
Epoch   0 Batch  271/137861 - Train Accu

Epoch   0 Batch  347/137861 - Train Accuracy:  0.000, Validation Accuracy:  0.059, Loss:  4.092
Epoch   0 Batch  348/137861 - Train Accuracy:  0.059, Validation Accuracy:  0.118, Loss:  4.349
Epoch   0 Batch  349/137861 - Train Accuracy:  0.059, Validation Accuracy:  0.176, Loss:  3.915
Epoch   0 Batch  350/137861 - Train Accuracy:  0.111, Validation Accuracy:  0.176, Loss:  4.018
Epoch   0 Batch  351/137861 - Train Accuracy:  0.059, Validation Accuracy:  0.118, Loss:  4.224
Epoch   0 Batch  352/137861 - Train Accuracy:  0.000, Validation Accuracy:  0.059, Loss:  4.120
Epoch   0 Batch  353/137861 - Train Accuracy:  0.167, Validation Accuracy:  0.000, Loss:  3.947
Epoch   0 Batch  354/137861 - Train Accuracy:  0.118, Validation Accuracy:  0.000, Loss:  4.145
Epoch   0 Batch  355/137861 - Train Accuracy:  0.000, Validation Accuracy:  0.000, Loss:  5.300
Epoch   0 Batch  356/137861 - Train Accuracy:  0.118, Validation Accuracy:  0.000, Loss:  3.892
Epoch   0 Batch  357/137861 - Train Accu

...

Epoch   0 Batch 85765/137861 - Train Accuracy:  0.000, Validation Accuracy:  0.059, Loss:  4.333
Epoch   0 Batch 85766/137861 - Train Accuracy:  0.000, Validation Accuracy:  0.059, Loss:  2.993
Epoch   0 Batch 85767/137861 - Train Accuracy:  0.059, Validation Accuracy:  0.059, Loss:  3.454
Epoch   0 Batch 85768/137861 - Train Accuracy:  0.053, Validation Accuracy:  0.059, Loss:  3.517
Epoch   0 Batch 85769/137861 - Train Accuracy:  0.056, Validation Accuracy:  0.059, Loss:  3.245
Epoch   0 Batch 85770/137861 - Train Accuracy:  0.059, Validation Accuracy:  0.059, Loss:  3.482
Epoch   0 Batch 85771/137861 - Train Accuracy:  0.053, Validation Accuracy:  0.059, Loss:  3.966
Epoch   0 Batch 85772/137861 - Train Accuracy:  0.059, Validation Accuracy:  0.059, Loss:  3.417
Epoch   0 Batch 85773/137861 - Train Accuracy:  0.056, Validation Accuracy:  0.059, Loss:  3.289
Epoch   0 Batch 85774/137861 - Train Accuracy:  0.000, Validation Accuracy:  0.059, Loss:  3.244
Epoch   0 Batch 85775/137861 -

Epoch   0 Batch 85851/137861 - Train Accuracy:  0.059, Validation Accuracy:  0.059, Loss:  3.322
Epoch   0 Batch 85852/137861 - Train Accuracy:  0.000, Validation Accuracy:  0.059, Loss:  3.142
Epoch   0 Batch 85853/137861 - Train Accuracy:  0.000, Validation Accuracy:  0.059, Loss:  3.509
Epoch   0 Batch 85854/137861 - Train Accuracy:  0.000, Validation Accuracy:  0.059, Loss:  3.447
Epoch   0 Batch 85855/137861 - Train Accuracy:  0.000, Validation Accuracy:  0.059, Loss:  4.541
Epoch   0 Batch 85856/137861 - Train Accuracy:  0.059, Validation Accuracy:  0.059, Loss:  3.363
Epoch   0 Batch 85857/137861 - Train Accuracy:  0.059, Validation Accuracy:  0.059, Loss:  3.389
Epoch   0 Batch 85858/137861 - Train Accuracy:  0.000, Validation Accuracy:  0.059, Loss:  4.506
Epoch   0 Batch 85859/137861 - Train Accuracy:  0.000, Validation Accuracy:  0.059, Loss:  3.428
Epoch   0 Batch 85860/137861 - Train Accuracy:  0.056, Validation Accuracy:  0.059, Loss:  3.027
Epoch   0 Batch 85861/137861 -

Epoch   0 Batch 85939/137861 - Train Accuracy:  0.000, Validation Accuracy:  0.059, Loss:  4.228
Epoch   0 Batch 85940/137861 - Train Accuracy:  0.118, Validation Accuracy:  0.059, Loss:  3.675
Epoch   0 Batch 85941/137861 - Train Accuracy:  0.000, Validation Accuracy:  0.059, Loss:  3.030
Epoch   0 Batch 85942/137861 - Train Accuracy:  0.059, Validation Accuracy:  0.059, Loss:  3.654
Epoch   0 Batch 85943/137861 - Train Accuracy:  0.000, Validation Accuracy:  0.059, Loss:  3.567
Epoch   0 Batch 85944/137861 - Train Accuracy:  0.059, Validation Accuracy:  0.059, Loss:  3.427
Epoch   0 Batch 85945/137861 - Train Accuracy:  0.000, Validation Accuracy:  0.059, Loss:  3.382
Epoch   0 Batch 85946/137861 - Train Accuracy:  0.059, Validation Accuracy:  0.059, Loss:  3.526
Epoch   0 Batch 85947/137861 - Train Accuracy:  0.111, Validation Accuracy:  0.059, Loss:  3.039
Epoch   0 Batch 85948/137861 - Train Accuracy:  0.000, Validation Accuracy:  0.059, Loss:  2.895
Epoch   0 Batch 85949/137861 -

Epoch   0 Batch 86027/137861 - Train Accuracy:  0.056, Validation Accuracy:  0.059, Loss:  3.128
Epoch   0 Batch 86028/137861 - Train Accuracy:  0.000, Validation Accuracy:  0.059, Loss:  3.751
Epoch   0 Batch 86029/137861 - Train Accuracy:  0.000, Validation Accuracy:  0.059, Loss:  3.479
Epoch   0 Batch 86030/137861 - Train Accuracy:  0.000, Validation Accuracy:  0.059, Loss:  2.683
Epoch   0 Batch 86031/137861 - Train Accuracy:  0.059, Validation Accuracy:  0.059, Loss:  3.296
Epoch   0 Batch 86032/137861 - Train Accuracy:  0.053, Validation Accuracy:  0.059, Loss:  3.471
Epoch   0 Batch 86033/137861 - Train Accuracy:  0.000, Validation Accuracy:  0.059, Loss:  3.199
Epoch   0 Batch 86034/137861 - Train Accuracy:  0.000, Validation Accuracy:  0.059, Loss:  3.195
Epoch   0 Batch 86035/137861 - Train Accuracy:  0.053, Validation Accuracy:  0.059, Loss:  3.652
Epoch   0 Batch 86036/137861 - Train Accuracy:  0.000, Validation Accuracy:  0.059, Loss:  3.214
Epoch   0 Batch 86037/137861 -

Epoch   0 Batch 86113/137861 - Train Accuracy:  0.000, Validation Accuracy:  0.059, Loss:  3.037
Epoch   0 Batch 86114/137861 - Train Accuracy:  0.000, Validation Accuracy:  0.059, Loss:  2.970
Epoch   0 Batch 86115/137861 - Train Accuracy:  0.000, Validation Accuracy:  0.059, Loss:  3.366
Epoch   0 Batch 86116/137861 - Train Accuracy:  0.059, Validation Accuracy:  0.059, Loss:  3.002
Epoch   0 Batch 86117/137861 - Train Accuracy:  0.000, Validation Accuracy:  0.059, Loss:  3.237
Epoch   0 Batch 86118/137861 - Train Accuracy:  0.059, Validation Accuracy:  0.059, Loss:  6.229
Epoch   0 Batch 86119/137861 - Train Accuracy:  0.059, Validation Accuracy:  0.059, Loss:  3.187
Epoch   0 Batch 86120/137861 - Train Accuracy:  0.000, Validation Accuracy:  0.059, Loss:  2.927
Epoch   0 Batch 86121/137861 - Train Accuracy:  0.000, Validation Accuracy:  0.059, Loss:  3.328
Epoch   0 Batch 86122/137861 - Train Accuracy:  0.111, Validation Accuracy:  0.059, Loss:  4.122
Epoch   0 Batch 86123/137861 -

### Save Parameters
Save the `batch_size` and `save_path` parameters for inference.

In [ ]:
"""
DON'T MODIFY ANYTHING IN THIS CELL
"""
# Save parameters for checkpoint
helper.save_params(save_path)

# Checkpoint

In [ ]:
"""
DON'T MODIFY ANYTHING IN THIS CELL
"""
import tensorflow as tf
import numpy as np
import helper
import problem_unittests as tests

_, (source_vocab_to_int, target_vocab_to_int), (source_int_to_vocab, target_int_to_vocab) = helper.load_preprocess()
load_path = helper.load_params()

## Sentence to Sequence
To feed a sentence into the model for translation, you first need to preprocess it.  Implement the function `sentence_to_seq()` to preprocess new sentences.

- Convert the sentence to lowercase
- Convert words into ids using `vocab_to_int`
- Convert words not in the vocabulary, to the `<UNK>` word id.

In [ ]:
def sentence_to_seq(sentence, vocab_to_int):
    """
    Convert a sentence to a sequence of ids
    :param sentence: String
    :param vocab_to_int: Dictionary to go from the words to an id
    :return: List of word ids
    """
    # TODO: Implement Function
    return None


"""
DON'T MODIFY ANYTHING IN THIS CELL THAT IS BELOW THIS LINE
"""
tests.test_sentence_to_seq(sentence_to_seq)

## Translate
This will translate `translate_sentence` from English to French.

In [ ]:
translate_sentence = 'he saw a old yellow truck .'


"""
DON'T MODIFY ANYTHING IN THIS CELL
"""
translate_sentence = sentence_to_seq(translate_sentence, source_vocab_to_int)

loaded_graph = tf.Graph()
with tf.Session(graph=loaded_graph) as sess:
    # Load saved model
    loader = tf.train.import_meta_graph(load_path + '.meta')
    loader.restore(sess, load_path)

    input_data = loaded_graph.get_tensor_by_name('input:0')
    logits = loaded_graph.get_tensor_by_name('logits:0')
    keep_prob = loaded_graph.get_tensor_by_name('keep_prob:0')

    translate_logits = sess.run(logits, {input_data: [translate_sentence], keep_prob: 1.0})[0]

print('Input')
print('  Word Ids:      {}'.format([i for i in translate_sentence]))
print('  English Words: {}'.format([source_int_to_vocab[i] for i in translate_sentence]))

print('\nPrediction')
print('  Word Ids:      {}'.format([i for i in np.argmax(translate_logits, 1)]))
print('  French Words: {}'.format([target_int_to_vocab[i] for i in np.argmax(translate_logits, 1)]))

## Imperfect Translation
You might notice that some sentences translate better than others.  Since the dataset you're using only has a vocabulary of 227 English words of the thousands that you use, you're only going to see good results using these words.  Additionally, the translations in this data set were made by Google translate, so the translations themselves aren't particularly good.  (We apologize to the French speakers out there!) Thankfully, for this project, you don't need a perfect translation. However, if you want to create a better translation model, you'll need better data.

You can train on the [WMT10 French-English corpus](http://www.statmt.org/wmt10/training-giga-fren.tar).  This dataset has more vocabulary and richer in topics discussed.  However, this will take you days to train, so make sure you've a GPU and the neural network is performing well on dataset we provided.  Just make sure you play with the WMT10 corpus after you've submitted this project.
## Submitting This Project
When submitting this project, make sure to run all the cells before saving the notebook. Save the notebook file as "dlnd_language_translation.ipynb" and save it as a HTML file under "File" -> "Download as". Include the "helper.py" and "problem_unittests.py" files in your submission.